In [1]:
import sys
import os

# Get the root directory of the project
project_root = os.path.abspath(os.path.join(os.getcwd(), '..'))

# Add the root directory to the system path
sys.path.insert(0, project_root)

In [2]:
import pandas as pd 
import os
import json

import torch
from torch.utils.data import Dataset, DataLoader
from transformers import AutoTokenizer

# import seaborn as sns
# sns.set_theme()

In [3]:
from explainable_dataset import *
from viz_utils import create_highlighted_passage
from IPython.display import display, HTML

def highlight_passage(tokens, binary_list):
    highlighted_passage = create_highlighted_passage(tokens,
                                                     binary_list,
                                                     None,
                                                     'green',
                                                     'linear')
    display(HTML("\n".join(highlighted_passage)))
    
tokenizer = AutoTokenizer.from_pretrained('meta-llama/Llama-3.1-70B-Instruct')


file_path = '../data/35_random_samples_explained.jsonl'
dataset_me = ExplanationsDataset(file_path, tokenizer, decode_positive_as_list=True)

file_path = '../data/35_random_samples_llama3.1:70b-instruct-q8_0.jsonl'
dataset_llama = ExplanationsDataset(file_path, tokenizer, decode_positive_as_list=True)

# Iterate through the data
for i in range(len(dataset_llama)):
    print(dataset_me[i]["query"])
    
    print("Me")
    d = dataset_me[i]
    highlight_passage(d['tokenized_positive_decoded'], d['rationales'])
    
    print("Llma")  
    d = dataset_llama[i]
    highlight_passage(d['tokenized_positive_decoded'], d['rationales'])
    
    print("\n")

what is a system hardware
Me


Llma




meaning of the name lincoln
Me


Llma




do.muslims not believe the holocaust happened
Me


...

Llma




what is principal company
Me


Llma




how do i move information from my old outlook emails to new computer
Me


Llma


In [4]:

dataset_paths = [
    '35_random_samples_explained.jsonl',
    '35_random_samples_gemma2:27b-instruct-q8_0.jsonl',
    '35_random_samples_gemma2:9b-instruct-q8_0.jsonl',
    '35_random_samples_gpt-4o-mini-2024-07-18.jsonl',
    '35_random_samples_gpt-4o-2024-08-06.jsonl',
    '35_random_samples_llama3.1:70b-instruct-q4_0.jsonl',
    '35_random_samples_llama3.1:70b-instruct-q8_0.jsonl',
    '35_random_samples_llama3.1:8b-instruct-fp16.jsonl',
]

datasets = {}
for dataset_path in dataset_paths:
    dataset_path = "../data/" + dataset_path
    d = ExplanationsDataset(dataset_path, tokenizer, decode_positive_as_list=True)
    dataset_name = dataset_path.removeprefix("../data/35_random_samples_").removesuffix(".jsonl")
    datasets[dataset_name] = d

datasets

{'explained': <explainable_dataset.ExplanationsDataset at 0x7fa713c57cd0>,
 'gemma2:27b-instruct-q8_0': <explainable_dataset.ExplanationsDataset at 0x7fa713ca7dd0>,
 'gemma2:9b-instruct-q8_0': <explainable_dataset.ExplanationsDataset at 0x7fa713c6ed10>,
 'gpt-4o-mini-2024-07-18': <explainable_dataset.ExplanationsDataset at 0x7fa713c3c850>,
 'gpt-4o-2024-08-06': <explainable_dataset.ExplanationsDataset at 0x7fa713cd5750>,
 'llama3.1:70b-instruct-q4_0': <explainable_dataset.ExplanationsDataset at 0x7fa713cbb590>,
 'llama3.1:70b-instruct-q8_0': <explainable_dataset.ExplanationsDataset at 0x7fa713abd650>,
 'llama3.1:8b-instruct-fp16': <explainable_dataset.ExplanationsDataset at 0x7fa713ac70d0>}

In [5]:
def read_tf_idf_data():
    file_path = '../data/35_random_samples_tf_idf.jsonl'
    with open(file_path, 'r') as f:
        data = [json.loads(line) for line in f]
    return data

tf_idf_data = read_tf_idf_data()

In [6]:
import pandas as pd

# Initialize the DataFrame to hold the data
columns = ['query']  # Start with 'query'
# Add columns dynamically based on the dataset keys
columns.extend([f"tokenized_positive_decoded_{key}" for key in datasets.keys()])
columns.extend([f"rationales_{key}" for key in datasets.keys()])

df = pd.DataFrame(columns=columns)

# Assuming all datasets have the same length
for i in range(len(next(iter(datasets.values())))):  # Use length of the first dataset
    row_data = {'query': datasets[next(iter(datasets))][i]['query']}  # Initialize with query
    
    # Iterate through each dataset in the dictionary
    for key, dataset in datasets.items():
        row_data[f"tokenized_positive_decoded_{key}"] = dataset[i]['tokenized_positive_decoded']
        row_data[f"rationales_{key}"] = dataset[i]['rationales']
    
    # Add tf-idf data
    row_data['rationales_tf_idf'] = torch.tensor(tf_idf_data[i]['score_mask'])
    row_data['rationales_select_all'] = torch.tensor(tf_idf_data[i]['select_all'])
    
    # Append the data to the DataFrame
    df = pd.concat([df, pd.DataFrame([row_data])], ignore_index=True)

    

# Output the DataFrame
df


query  \
0                           what is a system hardware   
1                         meaning of the name lincoln   
2       do.muslims not believe the holocaust happened   
3           what illness do premature babies contract   
4                 what is the usual dose of lorazepam   
5        what is the average salary for payroll clerk   
6                         lymphocyte rel normal range   
7       how much alcohol is in a mike's hard lemonade   
8                what university is the raging cajuns   
9              the  number one visited amusement park   
10                              what is preceptor pay   
11          behavioral medicine psychology definition   
12                    where is a town called tightwad   
13                          how long is roatan island   
14      how to increase water pressure on shower head   
15                              necklacing definition   
16                            oophorectomy definition   
17           is mitochondria in plant or animal cells   
18                        cost of disney memory maker   
19                       what county is wanship ut in   
20                               what does dike mean?   
21                         hybrid material definition   
22               what type of animal i called a queen   
23                            how is stucco installed   
24  how long do i need to keep records for self as...   
25        what is forty four wedding anniversary gift   
26                        average rn salary boston ma   
27  what types of things does facilitated diffusio...   
28      vitamin d deficiency symptoms in women causes   
29                          what is college is temple   
30                  what county is madison florida in   
31                             largest trade partners   
32               labor cost to install laminate floor   
33                          what is principal company   
34  how do i move information from my old outlook ...   

                 tokenized_positive_decoded_explained  \
0   [Abb, rev, iated,  as,  HW, ,,  Hardware,  is,...   
1   [American,  Meaning, :,  The,  name,  Lincoln,...   
2   [For,  the,  majority,  of,  Muslims,  in,  th...   
3   [Prem, ature,  birth,  can,  lead,  to,  these...   
4   [At, ivan,  Dos, age,  For,  Adults, .,  The, ...   
5   [Pay, roll,  Clerk,  Salary, .,  The,  average...   
6   [The,  normal,  range,  of,  lymph, ocytes,  i...   
7   [Mike, 's,  Hard,  Lemon, ade,  is,  , 5, ., 2...   
8   [The,  Louisiana,  Rag, in, ',  Caj, uns,  bas...   
9   [World, 's,  Most, -, Visited,  Theme,  Parks,...   
10  [Pre, ceptor,  payments,  are,  token,  paymen...   
11  [Behavior, al,  medicine,  is,  an,  interdisc...   
12  [T, ight, w, ad,  is,  a,  village,  in,  Henr...   
13  [Ro, atan,  is,  , 32,  miles,  long,  and,  v...   
14  [Go,  to,  your,  local,  home,  improvement, ...   
15  [Free, base,  (, 0, ., 00,  /,  , 0,  votes, )...   
16  [O, oph, ore, ct, omy,  definition, ,,  the,  ...   
17  [Mit, ochond, ria,  are,  rod,  shaped,  struc...   
18  [(P, urch, asing,  the,  new,  service,  at,  ...   
19  [W, anship, ,,  Utah, :,  Land, ,,  Ranch, es,...   
20  [The,  term,  dy, ke,  or,  di, ke,  is,  a,  ...   
21  [Hy, brid,  material, .,  Hybrid,  materials, ...   
22  [Ant, s,  live,  in,  colonies,  where,  one, ...   
23  [Steven,  Bliss, .,  St, ucc, o,  on,  buildin...   
24  [But,  for,  businesses,  you,  will,  need,  ...   
25  [The,  modern,  gift,  for,  your,  forty, -fo...   
26  [The,  Boston, -C, am, bridge, -, Qu, incy, ,,...   
27  [Fac, ilit, ated,  diffusion,  is,  the,  flow...   
28  [Other,  Signs,  and,  Symptoms, .,  Fat, igue...   
29  [Tem, ple,  College,  is,  a,  public,  instit...   
30  [Mad, ison, ,,  Florida, .,  Madison,  is,  a,...   
31  [Top,  , 10,  trading,  partners,  of,  the,  ...   
32  [Our,  free,  calculator,  uses,  recent, ,,  ...   
33  [In,  business, ,,  a,  principal,  is,  a,  p...   


In [7]:
from sklearn.metrics import precision_score, recall_score, f1_score
import pandas as pd


def compute_stats(rationales_label):
    # Initialize variables to store the cumulative metrics
    precisions = []
    recalls = []
    f1_scores = []

    # Iterate through each row in the DataFrame
    for index, row in df.iterrows():
        # Get the rationales from both datasets
        rationales_llama = row["rationales_" + rationales_label]
        rationales_me = row['rationales_explained']

        y_true = rationales_me.tolist()
        y_pred = rationales_llama.tolist() 

        # Calculate precision, recall, and F1 score for this pair of rationales
        try:
            precision = precision_score(y_true, y_pred)
            recall = recall_score(y_true, y_pred)
            f1 = f1_score(y_true, y_pred)
        except ValueError as e:
            print(f"{index}: {e}")
            print()
            continue
        # Append the scores to the lists
        precisions.append(precision)
        recalls.append(recall)
        f1_scores.append(f1)

    # Calculate the average of each metric
    avg_precision = sum(precisions) / len(precisions)
    avg_recall = sum(recalls) / len(recalls)
    avg_f1 = sum(f1_scores) / len(f1_scores)

    return {
        'avg_f1': avg_f1,
        'avg_precision': avg_precision,
        'avg_recall': avg_recall,
        'f1_scores': f1_scores,
        'precisions': precisions,
        'recalls': recalls
    }

    
all_stats = {}
for model_name in datasets.keys():
    all_stats[model_name] = compute_stats(model_name)
    
all_stats['tf_idf'] = compute_stats('tf_idf')
all_stats['select_all'] = compute_stats('select_all')

all_stats = {k:v for k, v in sorted(all_stats.items(), key=lambda item: -item[1]['avg_f1'])}
for method, stats in all_stats.items():
    print(f"\n\tStats for {method}")
    print(f"F1 Score: {stats['avg_f1']:.4f}")
    print(f"Precision Score: {stats['avg_precision']:.4f}")
    print(f"Recall Score: {stats['avg_recall']:.4f}")

          
save_stats = True
if save_stats:
    with open("../data/other/f1_stats.json", "w") as file:
          json.dump(all_stats, file, indent=4)
          

/mnt/data/xjarol06_firllm/conda/envs/llm2colbert/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/mnt/data/xjarol06_firllm/conda/envs/llm2colbert/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/mnt/data/xjarol06_firllm/conda/envs/llm2colbert/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f


	Stats for explained
F1 Score: 1.0000
Precision Score: 1.0000
Recall Score: 1.0000

	Stats for gemma2:27b-instruct-q8_0
F1 Score: 0.7045
Precision Score: 0.7592
Recall Score: 0.7093

	Stats for gpt-4o-2024-08-06
F1 Score: 0.6456
Precision Score: 0.7667
Recall Score: 0.6197

	Stats for llama3.1:70b-instruct-q8_0
F1 Score: 0.6415
Precision Score: 0.7495
Recall Score: 0.6587

	Stats for llama3.1:70b-instruct-q4_0
F1 Score: 0.6376
Precision Score: 0.7587
Recall Score: 0.6371

	Stats for gpt-4o-mini-2024-07-18
F1 Score: 0.6202
Precision Score: 0.6823
Recall Score: 0.6959

	Stats for llama3.1:8b-instruct-fp16
F1 Score: 0.5446
Precision Score: 0.5977
Recall Score: 0.6042

	Stats for select_all
F1 Score: 0.4643
Precision Score: 0.3249
Recall Score: 1.0000

	Stats for gemma2:9b-instruct-q8_0
F1 Score: 0.4249
Precision Score: 0.6883
Recall Score: 0.3654

	Stats for tf_idf
F1 Score: 0.2373
Precision Score: 0.5264
Recall Score: 0.1716


In [8]:
# viz_datasets = [] # to see all
viz_datasets = ['gemma2:27b-instruct-q8_0', 'gemma2:9b-instruct-q8_0', 'explained']

viz_indexes = [] # to see all
# viz_indexes = [31, 26]

for i in range(len(dataset_llama)):
    if i not in viz_indexes and viz_indexes != []:
        continue
    
    print(f"{'X' * 20}  {datasets['explained'][i]['query']}  {'X' * 20}")
    for model_name, dataset in datasets.items():
        if model_name not in viz_datasets and viz_datasets != []:
            continue
            
        print(f"\t{model_name}")
        d = dataset[i]
        highlight_passage(d['tokenized_positive_decoded'], d['rationales'])

        print()
    print()
    print()
        

XXXXXXXXXXXXXXXXXXXX  what is a system hardware  XXXXXXXXXXXXXXXXXXXX
	explained



	gemma2:27b-instruct-q8_0



	gemma2:9b-instruct-q8_0





XXXXXXXXXXXXXXXXXXXX  meaning of the name lincoln  XXXXXXXXXXXXXXXXXXXX
	explained



	gemma2:27b-instruct-q8_0


...


	gemma2:27b-instruct-q8_0



	gemma2:9b-instruct-q8_0





XXXXXXXXXXXXXXXXXXXX  how do i move information from my old outlook emails to new computer  XXXXXXXXXXXXXXXXXXXX
	explained



	gemma2:27b-instruct-q8_0



	gemma2:9b-instruct-q8_0


In [19]:
def get_selected_lens(explanations):
    return pd.Series(
    [
        len([x for x in xs if x == 1])
        for xs 
        in explanations
    ]
    )

all_rationales = [col_name for col_name in df.columns.values if col_name.startswith("rationales_")]
for rationale_name in all_rationales:

    print(f"\n\tLenghts of explanations {rationale_name} statistics:")
    explanations = df[rationale_name]
    print(get_selected_lens(explanations).describe())
    



	Lenghts of explanations rationales_explained statistics:
count     35.000000
mean      24.285714
std       19.283598
min        4.000000
25%       12.500000
50%       21.000000
75%       31.000000
max      105.000000
dtype: float64

	Lenghts of explanations rationales_gemma2:27b-instruct-q8_0 statistics:
count    35.000000
mean     21.542857
std      12.327260
min       2.000000
25%      13.500000
50%      19.000000
75%      29.000000
max      57.000000
dtype: float64

	Lenghts of explanations rationales_gemma2:9b-instruct-q8_0 statistics:
count    35.000000
mean     12.800000
std      10.585228
min       0.000000
25%       3.000000
50%      12.000000
75%      20.000000
max      36.000000
dtype: float64

	Lenghts of explanations rationales_gpt-4o-mini-2024-07-18 statistics:
count    35.000000
mean     25.914286
std      15.416514
min       2.000000
25%      15.500000
50%      24.000000
75%      37.000000
max      59.000000
dtype: float64

	Lenghts of explanations rationales_gpt-4o-20

['rationales_explained',
 'rationales_gemma2:27b-instruct-q8_0',
 'rationales_gemma2:9b-instruct-q8_0',
 'rationales_gpt-4o-mini-2024-07-18',
 'rationales_gpt-4o-2024-08-06',
 'rationales_llama3.1:70b-instruct-q4_0',
 'rationales_llama3.1:70b-instruct-q8_0',
 'rationales_llama3.1:8b-instruct-fp16',
 'rationales_tf_idf',
 'rationales_select_all']